In [55]:
import numpy as np
import sys
#data = np.load('results/GEN_Ours_ccif_1719876542/out.npy') # 128 ckpt_0.000000_1530000.pt
data = np.load('out.npy') # 1024 ckpt_0.000000_1530000.pt

#data = np.load('results/GEN_Ours_ccif_1719842653/out.npy')results/GEN_Ours_ccif_1719876969/out.npyq
#data = np.load('results/GEN_Ours_ccif_1719839490/out.npy') #results/GEN_Ours_airplane_1716864944/out.npy') #GEN_Ours_airplane_1716881180
#data = np.load('results/GEN_Ours_airplane_1716864944/out.npy')
               #　data = np.load('out.npy')
# !ckpt_0.000000_100000.pt 3hour of trainig by gefeorce 3090
num,nsize,xdeg=data.shape
print(data.shape)


rfac=3
densitymap=True

#onlybatch1=True
#if(onlybatch1):
#    data=data[0:1,0:nsize,0:3] 
#else:
#    data=data.reshape(1,num*nsize,3)

print(data.shape)
#import time
#import matplotlib.pyplot as plt
#from mpl_toolkits.mplot3d import proj3d

#for i in range(1):
#    x = data[i,:,0]
#    y = data[i,:,1]
#    z = data[i,:,2]
#    fig = plt.figure(figsize=(8, 8))
#    ax = fig.add_subplot(111, projection='3d', proj_type='ortho')
#    #Plot with very small marker
#    ax.scatter(x, y, z, s=0.5)
#    #plt.show()

data=rfac*data
#print(data.shape)
#print(datax.shape)
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd
#print(data.shape)
idx=8
for id in range(0,idx): #idx,idx+1):
    ndat=data[id,:,:].shape[0]
    #print(ndat,data[id,:,:].shape[1])
    datax=np.zeros((ndat,4))
    distance=np.zeros((ndat))
    datax[0:ndat,0:3]=data[id,0:ndat,0:3]
    #break
    for ip in range(0,datax.shape[0]):
       dis=np.sum(np.array(data[id,ip,0:3])**2)**0.5
       
#############################
       #dis=0 if ip>2048 else 1
       #dis=2 if ip>4096 else dis
       #if(ip==0): dis=3resume
#############################       
       
       datax[ip,3]=dis
       #if(dis>3.3):datax[ip,3]=100
       distance[ip]=dis

    distance.sort()
    #mask=(distance>0.1)
    #distance=distance[mask]
    old=0
    ncount=0
    for i in range(0,distance.shape[0]):
        ncount=ncount+1
        if(distance[i]>old+0.1):
          #print(old,ncount)
          old=distance[i]
          ncount=0

    mmm=8

    if densitymap: # Create density map
        x = np.linspace(-mmm, mmm, 50)
        y = np.linspace(-mmm, mmm, 50)
        z = np.linspace(-mmm, mmm, 50)
        x, y, z = np.meshgrid(x, y, z)
        
        for i in range(0,ndat):
            xc=datax[i,0]
            yc=datax[i,1]
            zc=datax[i,2]
            rr=.3
            densityadd =np.exp(-(x-xc)**2/rr + -(y-yc)**2/rr + -(z-zc)**2/rr)
            if(i==0): 
                density = densityadd
            else:
                density = densityadd + density
        # Create a 3D surface plot
        fig = go.Figure(data=go.Volume(
            x=x.flatten(),
            y=y.flatten(),
            z=z.flatten(),
            value=density.flatten(),
            isomin=10,
            isomax=50.0,
            opacity=0.1,  # needs to be small to see through all surfaces
            surface_count=10,  # number of isosurfaces, 2 by default
        ))

        # Set plot title and axis labels
        fig.update_layout(
            title='Density map)',
            scene=dict(
                xaxis_title='X',
                yaxis_title='Y',
                zaxis_title='Z'
            )
        )          

        fig.update_layout(width=800, height=800)
        fig.write_html("./zeolite_sampling_density."+str(id)+".html")
        #fig.show()
    #    continue
    
    #print('id=',id,'len=',len(datax) ,datax.shape)
    # データフレームのデータを描画する
    df  = pd.DataFrame(datax,columns=['x','y','z','cc'])
    fig = px.scatter_3d(df, x='x', y='y', z='z', color='cc')
    # Set aspect ratio to be equal
    mmm=8
    #projection orqtho
    fig.update_layout(scene=dict(camera=dict(projection=dict(type="orthographic"))))
    
    fig.update_layout(
    scene=dict(
        xaxis=dict(range=[-mmm, mmm]),
        yaxis=dict(range=[-mmm, mmm]),
        zaxis=dict(range=[-mmm, mmm]),
        aspectmode='cube'
    ))
    #プロットのサイズを変更
    #プロットのキャプションを変更
    #カラーバーのタイトルを変更
    fig.update_layout(coloraxis_colorbar=dict(title='Distance(Å)'))
    # fig.update_layout(title=\
    #     "Fig.1: A samping of {<B>r</B>} by p(<B>r</B>|<B>z</B>) for a 256-dimentional random latent vector <B>z</B>.<BR>\
    #     After we prepared Si-centerd 6192 clusters (within 6 Å, Si only) taken from Zeolite<BR>\
    #     database, we let Diffucion-Point-Cloud(DPC) learn <br>\
    #     the randomly-rotated clusters. <br>\
    #     The color represents the distance from the central Si.")
    fig.update_layout(width=800, height=800)
    fig.update_layout(scene_aspectmode='cube')
    #fig.update_traces(marker=dict(size=5))
    fig.update_traces(marker=dict(size=1))
    fig.write_html("./zeolite_sampling."+str(id)+".html")
    fig.show()


(8, 2048, 3)
(8, 2048, 3)
